In [7]:
import pandas as pd
import numpy as np
dati = pd.read_csv("C:\\Users\\Lenovo\\OneDrive\\Documenti\\Università\\Ricerca\\NFL kaggle challenge 2024\\data\\tracking_data_with_tackles(w1).csv")
giocate = pd.read_csv("C:\\Users\\Lenovo\\OneDrive\\Documenti\\Università\\Ricerca\\NFL kaggle challenge 2024\\data\\plays.csv")
partite = pd.read_csv("C:\\Users\\Lenovo\\OneDrive\\Documenti\\Università\\Ricerca\\NFL kaggle challenge 2024\\data\\games.csv")

In [3]:
max_frameId_totale = dati["frameId"].max() # massimo valore di frameId
max_frameI = dati.set_index(["gameId", "playId"])
max_frameI = max_frameI["frameId"].groupby(by=["gameId", "playId"]).max()
max_frameI.head() # il massimo valore di frameId per il ogni giocata

gameId      playId
2022090800  56        22
            80        30
            101       49
            122       33
            146       56
Name: frameId, dtype: int64

In [16]:
# PRENDO TUTTE LE PARTITE (GAMEID) IN CUI HANNO GIOCATO I BUF
filtering = (partite["visitorTeamAbbr"] == "BUF") | (partite["homeTeamAbbr"] == "BUF")
BUF_gameId = partite.loc[filtering]["gameId"] 

In [17]:
dati.loc[dati["playDirection"] == "left", "playDirection"] = 1
dati.loc[dati["playDirection"] == "right", "playDirection"] = 0

dati.set_index(["gameId", "playId", "frameId"], inplace=True)
dati.sort_index(inplace=True)

In [54]:
giocate["gameClock"] = giocate["gameClock"].str.replace(":", ".").astype("double")
giocate.set_index(["gameId", "playId"], inplace=True)
giocate.sort_index(inplace=True)
giocate.head()

ballCarrierId ballCarrierDisplayName  \
gameId     playId                                         
2022090800 56              42489           Stefon Diggs   
           80              46076             Josh Allen   
           101             47857       Devin Singletary   
           122             47857       Devin Singletary   
           146             47857       Devin Singletary   

                                                     playDescription  quarter  \
gameId     playId                                                               
2022090800 56      (15:00) (Shotgun) J.Allen pass short right to ...        1   
           80      (14:29) (No Huddle, Shotgun) J.Allen scrambles...        1   
           101     (13:54) D.Singletary right end to BUF 45 for 7...        1   
           122     (13:15) (Shotgun) J.Allen pass short right to ...        1   
           146     (12:33) (Shotgun) D.Singletary left tackle to ...        1   

                   down  yardsToGo possessionTeam defensiveTeam yardlineSide  \
gameId     playId                                                              
2022090800 56         1         10            BUF            LA          BUF   
           80         2          4            BUF            LA          BUF   
           101        1         10            BUF            LA          BUF   
           122        2          3            BUF            LA          BUF   
           146        1         10            BUF            LA           LA   

                   yardlineNumber  ...  preSnapHomeTeamWinProbability  \
gameId     playId                  ...                                  
2022090800 56                  25  ...                       0.413347   
           80                  31  ...                       0.413316   
           101                 38  ...                       0.399819   
           122                 45  ...                       0.384969   
           146                 49  ...                       0.365938   

                   preSnapVisitorTeamWinProbability  \
gameId     playId                                     
2022090800 56                              0.586653   
           80                              0.586684   
           101                             0.600181   
           122                             0.615031   
           146                             0.634062   

                   homeTeamWinProbabilityAdded visitorTeamWinProbilityAdded  \
gameId     playId                                                             
2022090800 56                        -0.000031                     0.000031   
           80                        -0.013497                     0.013497   
           101                       -0.014850                     0.014850   
           122                       -0.019032                     0.019032   
           146                        0.021616                    -0.021616   

                   expectedPoints  expectedPointsAdded  foulName1  foulName2  \
gameId     playId                                                              
2022090800 56            1.298699             0.004420        NaN        NaN   
           80            1.303119             0.823571        NaN        NaN   
           101           2.126690             0.562363        NaN        NaN   
           122           2.689053             0.399209        NaN        NaN   
           146           3.088262            -0.514056        NaN        NaN   

                  foulNFLId1  foulNFLId2  
gameId     playId                         
2022090800 56            NaN         NaN  
           80            NaN         NaN  
           101           NaN         NaN  
           122           NaN         NaN  
           146           NaN         NaN  

[5 rows x 33 columns]

In [27]:
# CELLA IMPORTANTE FILTRO TUTTI I DATI PER LE PARTITE IN CUI HANNO GIOCATO I BUF E RIASSEGNO IL DATASET FILTRATO A dati
dati = dati[dati.index.isin(BUF_gameId, level=0)]

In [63]:
grafo_dati = {}

for p in dati.index:
	mat_adj = np.ones(shape=(23, 23))
	s = dati.xs(p)
	clubs = s["club"][s["club"] != "football"]
    
	for i, club1 in enumerate(clubs):
		for j, club2 in enumerate(clubs):
			if club1 != club2:
				mat_adj[i, j] = 0
				mat_adj[j, i] = 0

	grafo_dati[p] = {
		"node_fts" : s.loc[:,["x", "y", "s", "a", "dis", "o", "dir"]].to_numpy(),
		"edge_fts" : mat_adj,
		"graph_fts" : giocate.loc[(p[0], p[1]), ["quarter", "down", "yardsToGo", "yardlineNumber", "gameClock"]].to_numpy(),
		"label": np.unique(dati["tackle"].xs(p))
	}
                  

In [64]:
grafo_dati

{(2022090800,
  56,
  1): {'node_fts': array([[8.83700000e+01, 2.72700000e+01, 1.62000000e+00, 1.15000000e+00,
          1.60000000e-01, 2.31740000e+02, 1.47900000e+02],
         [7.82500000e+01, 2.75300000e+01, 1.24000000e+00, 3.81000000e+00,
          1.10000000e-01, 4.20000000e+00, 3.31670000e+02],
         [9.10800000e+01, 3.16100000e+01, 3.91000000e+00, 2.34000000e+00,
          4.00000000e-01, 1.68330000e+02, 1.32020000e+02],
         [8.82500000e+01, 2.87400000e+01, 6.70000000e-01, 1.97000000e+00,
          7.00000000e-02, 2.44210000e+02, 3.02900000e+01],
         [8.06000000e+01, 3.82900000e+01, 6.23000000e+00, 9.00000000e-01,
          6.20000000e-01, 1.40050000e+02, 1.89380000e+02],
         [7.23400000e+01, 7.81000000e+00, 4.36000000e+00, 9.10000000e-01,
          4.30000000e-01, 3.38330000e+02, 2.57230000e+02],
         [7.79500000e+01, 4.07800000e+01, 5.50000000e+00, 3.00000000e+00,
          5.40000000e-01, 1.39540000e+02, 1.72500000e+02],
         [9.19900000e+01, 3.3780

In [14]:
giocate.set_index(["gameId", "playId"], inplace=True)
giocate.sort_index()
giocate.head()

ballCarrierId ballCarrierDisplayName  \
gameId     playId                                         
2022100908 3537            48723           Parker Hesse   
2022091103 3126            52457         Chase Claypool   
2022091111 1148            42547          Darren Waller   
2022100212 2007            46461             Mike Boone   
2022091900 1372            47857       Devin Singletary   

                                                     playDescription  quarter  \
gameId     playId                                                               
2022100908 3537    (7:52) (Shotgun) M.Mariota pass short middle t...        4   
2022091103 3126    (7:38) (Shotgun) C.Claypool right end to PIT 3...        4   
2022091111 1148    (8:57) D.Carr pass short middle to D.Waller to...        2   
2022100212 2007    (13:12) M.Boone left tackle to DEN 44 for 7 ya...        3   
2022091900 1372    (8:33) D.Singletary right guard to TEN 32 for ...        2   

                   down  yardsToGo possessionTeam defensiveTeam yardlineSide  \
gameId     playId                                                              
2022100908 3537       1         10            ATL            TB          ATL   
2022091103 3126       1         10            PIT           CIN          PIT   
2022091111 1148       2          5             LV           LAC           LV   
2022100212 2007       2         10            DEN            LV          DEN   
2022091900 1372       1         10            BUF           TEN          TEN   

                   yardlineNumber  ... preSnapHomeTeamWinProbability  \
gameId     playId                  ...                                 
2022100908 3537                41  ...                      0.976785   
2022091103 3126                34  ...                      0.160485   
2022091111 1148                30  ...                      0.756661   
2022100212 2007                37  ...                      0.620552   
2022091900 1372                35  ...                      0.836290   

                   preSnapVisitorTeamWinProbability  \
gameId     playId                                     
2022100908 3537                            0.023215   
2022091103 3126                            0.839515   
2022091111 1148                            0.243339   
2022100212 2007                            0.379448   
2022091900 1372                            0.163710   

                   homeTeamWinProbabilityAdded visitorTeamWinProbilityAdded  \
gameId     playId                                                             
2022100908 3537                      -0.006110                     0.006110   
2022091103 3126                      -0.010865                     0.010865   
2022091111 1148                      -0.037409                     0.037409   
2022100212 2007                      -0.002451                     0.002451   
2022091900 1372                       0.001053                    -0.001053   

                   expectedPoints  expectedPointsAdded  foulName1  foulName2  \
gameId     playId                                                              
2022100908 3537          2.360609             0.981955        NaN        NaN   
2022091103 3126          1.733344            -0.263424        NaN        NaN   
2022091111 1148          1.312855             1.133666        NaN        NaN   
2022100212 2007          1.641006            -0.043580        NaN        NaN   
2022091900 1372          3.686428            -0.167903        NaN        NaN   

                  foulNFLId1  foulNFLId2  
gameId     playId                         
2022100908 3537          NaN         NaN  
2022091103 3126          NaN         NaN  
2022091111 1148          NaN         NaN  
2022100212 2007          NaN         NaN  
2022091900 1372          NaN         NaN  

[5 rows x 33 columns]

In [66]:
import pickle

# save dictionary to person_data.pkl file
with open('C:\\Users\\Lenovo\\OneDrive\\Documenti\\Università\\Ricerca\\NFL kaggle challenge 2024\\data\\grafo_dati.pkl', 'wb') as fp:
    pickle.dump(grafo_dati, fp)
    print('grafo dati saved successfully to file')


dictionary saved successfully to file


In [67]:
grafo_dati.keys()

dict_keys([(2022090800, 56, 1), (2022090800, 56, 2), (2022090800, 56, 3), (2022090800, 56, 4), (2022090800, 56, 5), (2022090800, 56, 6), (2022090800, 56, 7), (2022090800, 56, 8), (2022090800, 56, 9), (2022090800, 56, 10), (2022090800, 56, 11), (2022090800, 56, 12), (2022090800, 56, 13), (2022090800, 56, 14), (2022090800, 56, 15), (2022090800, 56, 16), (2022090800, 56, 17), (2022090800, 56, 18), (2022090800, 56, 19), (2022090800, 56, 20), (2022090800, 56, 21), (2022090800, 56, 22), (2022090800, 80, 1), (2022090800, 80, 2), (2022090800, 80, 3), (2022090800, 80, 4), (2022090800, 80, 5), (2022090800, 80, 6), (2022090800, 80, 7), (2022090800, 80, 8), (2022090800, 80, 9), (2022090800, 80, 10), (2022090800, 80, 11), (2022090800, 80, 12), (2022090800, 80, 13), (2022090800, 80, 14), (2022090800, 80, 15), (2022090800, 80, 16), (2022090800, 80, 17), (2022090800, 80, 18), (2022090800, 80, 19), (2022090800, 80, 20), (2022090800, 80, 21), (2022090800, 80, 22), (2022090800, 80, 23), (2022090800, 80, 